# Import

In [1]:
import os
import numpy as np
import pandas as pd
import re
from struct import pack, unpack
import sys
import json
import pdb

! pip install --user -U nltk
import nltk
nltk.download('wordnet')
from nltk.tokenize import TweetTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.stem import PorterStemmer

[nltk_data] Downloading package wordnet to /home/amin/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# Data

In [2]:
! wget https://www.dropbox.com/s/y2w2vrs94y7kk5p/movies.csv

--2023-09-03 18:35:15--  https://www.dropbox.com/s/y2w2vrs94y7kk5p/movies.csv
Resolving www.dropbox.com (www.dropbox.com)... 162.125.11.18, 2620:100:6050:18::a27d:b12
Connecting to www.dropbox.com (www.dropbox.com)|162.125.11.18|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: /s/raw/y2w2vrs94y7kk5p/movies.csv [following]
--2023-09-03 18:35:15--  https://www.dropbox.com/s/raw/y2w2vrs94y7kk5p/movies.csv
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uc12a0926ee620fd39b1178739fe.dl.dropboxusercontent.com/cd/0/inline/CDB3sy9ff8liDkHkGBZhGZ9pZPgh1OHcZM3lJR_hMQtnkgvbZT2jiaMr3WnKV3yjkJzFKE_50xamih1G4z_zK2VS4cRe6sZVerruQ_UHW2qMSdh2F4vaok_vG-icpxGWFLOg-3zUHx93nZEeUFPB6niV/file# [following]
--2023-09-03 18:35:15--  https://uc12a0926ee620fd39b1178739fe.dl.dropboxusercontent.com/cd/0/inline/CDB3sy9ff8liDkHkGBZhGZ9pZPgh1OHcZM3lJR_hMQtnkgvbZT2jiaMr3WnKV3yjkJzFKE_50xamih1G4z_zK2VS4cRe6sZVerruQ_UHW2

In [3]:
d_path = './'
movie_df = pd.read_csv(d_path + 'movies.csv')
print('df.shpae:', movie_df.shape)
movie_df.head()

df.shpae: (6000, 3)


id                   title  \
0   1         The Suburbanite   
1   2            Laughing Gas   
2   3  A Calamitous Elopement   
3   4    The Call of the Wild   
4   5  A Lad from Old Ireland   

                                                plot  
0  The film is about a family who move to the sub...  
1  The plot is that of a black woman going to the...  
2  A young couple decides to elope after being ca...  
3  A white girl (Florence Lawrence) rejects a pro...  
4  An Irish boy (Olcott) emigrates to America to ...

In [4]:
def prepare_text(raw_text):
    """Preprocesses the text with tokenization, case folding, stemming and lemmatization

    Parameters
    ----------
    raw_text : str
        The title or plot of a movie

    Returns
    -------
    list
        A list of tokens
    """

    '''
        case folding
    '''
    lower_case_text = raw_text.lower()

    '''
        delete numbers
    '''
    out_number_text = re.sub('\d+', '', lower_case_text)

    '''
        tokenize
    '''
    tokenizer = nltk.RegexpTokenizer(r"\w+")
    tokenized_words = tokenizer.tokenize(out_number_text)
    
    '''
        lemmatization
        v: verb
        n: noun
        a: adjective
        r: adverb
        s: adj_sat
    '''
    
    lemmatized_words = []
    lemmatizer = WordNetLemmatizer()
    for word in tokenized_words:
        x = lemmatizer.lemmatize(word, pos='v')
        x = lemmatizer.lemmatize(x, pos='n')
        x = lemmatizer.lemmatize(x, pos='a')
        x = lemmatizer.lemmatize(x, pos='r')
        x = lemmatizer.lemmatize(x, pos='s')
        
        lemmatized_words.append(x)
    '''
        stemming
    '''

    stemmied_words = []
    stemmer = PorterStemmer()
    for word in lemmatized_words:
        stemmied_words.append(stemmer.stem(word))

    # TODO: tokenize, case_folding, stem, lemmatize
    # return ["edvard", "am", "a", "run", "he", "am", "always", "run"]
    return stemmied_words #lemmatized_words

prepare_text("Edvard was a Runner. He was always running.")

['edvard', 'be', 'a', 'runner', 'he', 'be', 'alway', 'run']

# Detecting and Eliminating Stop-Words

In [5]:
def get_stop_words(DataFrame, max_count):
    """Detects stop-words

    Parameters
    ----------
    DataFrame : Pandas DataFrame
        movie data frame
    
    max_count: count of words to show


    Returns
    -------
    dict
        A dictionary of terms with their repetition
    """
    words = {}
    df_size = DataFrame.shape[0]
    for i in range(df_size):
        arr_title = prepare_text(DataFrame.iloc[i]['title'])
        arr_plot = prepare_text(DataFrame.iloc[i]['plot'])

        for term in arr_title:
            if term in words.keys():
                words[term] += 1
            else:
                words[term] = 1

        for term in arr_plot:
            if term in words.keys():
                words[term] +=1
            else:
                words[term] = 1

    sorted_words = list(sorted(words.items(), key=lambda item: item[1], reverse=True))
    return sorted_words[:max_count]

stop_words_sorted  = get_stop_words(movie_df, 40)
print('most common words:')
stop_words_sorted

most common words:


[('the', 147470),
 ('to', 91732),
 ('a', 83715),
 ('and', 83270),
 ('be', 69098),
 ('of', 42862),
 ('in', 38985),
 ('hi', 34776),
 ('he', 32344),
 ('s', 31764),
 ('her', 28025),
 ('that', 26301),
 ('with', 25064),
 ('have', 20204),
 ('him', 18931),
 ('by', 17855),
 ('for', 17608),
 ('she', 17596),
 ('on', 14962),
 ('but', 13530),
 ('they', 13357),
 ('who', 12749),
 ('at', 12353),
 ('from', 11098),
 ('an', 10857),
 ('it', 10217),
 ('when', 9993),
 ('their', 9505),
 ('after', 8899),
 ('out', 8016),
 ('find', 7363),
 ('into', 7326),
 ('kill', 7203),
 ('up', 6995),
 ('take', 6911),
 ('them', 6558),
 ('go', 6396),
 ('leav', 6057),
 ('tell', 5741),
 ('one', 5467)]

In [15]:
'''
    use first 28 words for stop words
'''
stop_words = [k for k, v in stop_words_sorted[:28]]
print('stop words: ', stop_words)

stop words:  ['the', 'to', 'a', 'and', 'be', 'of', 'in', 'hi', 'he', 's', 'her', 'that', 'with', 'have', 'him', 'by', 'for', 'she', 'on', 'but', 'they', 'who', 'at', 'from', 'an', 'it', 'when', 'their']


In [16]:
def delete_stop_words_from_array(arr, stop_words):
    '''
        delete stop words from an array
    '''
    deleted_array = []
    for term in arr:
        if not term in stop_words:
            deleted_array.append(term)

    return deleted_array

def delete_stop_words(df, stop_words):
    
    '''
        df: pd.DataFrame
        stop_words: stop words (list)
        return: df without stop words
    '''

    d_df = pd.DataFrame(columns = df.columns)
    df_size = df.shape[0]
    for i in range(df_size):
        arr_title = prepare_text(df.iloc[i]['title'])
        arr_plot = prepare_text(df.iloc[i]['plot'])

        d_arr_title = []
        for term in arr_title:
            if not term in stop_words:
                d_arr_title.append(term)

        d_arr_plot = []
        for term in arr_plot:
            if not term in stop_words:
                d_arr_plot.append(term)

        d_df.loc[i] = [i, d_arr_title, d_arr_plot]

    return d_df

In [17]:
'''
    data frame with out stop words
'''

with_out_stop_words_df = delete_stop_words(movie_df, stop_words)

In [18]:
with_out_stop_words_df.head()

id                title                                               plot
0   0         [suburbanit]  [film, about, famili, move, suburb, hop, quiet...
1   1          [laugh, ga]  [plot, black, woman, go, dentist, toothach, gi...
2   2      [calamit, elop]  [young, coupl, decid, elop, after, catch, mids...
3   3         [call, wild]  [white, girl, florenc, lawrenc, reject, propos...
4   4  [lad, old, ireland]  [irish, boy, olcott, emigr, america, escap, de...

# Indexing

In [29]:
'''
    Positional_Index class
'''

class Positional_Index:

    def __init__(self):
        self.PI_title = {}
        self.PI_plot = {}
        self.df = pd.DataFrame(columns = ['id', 'title', 'plot'])


    '''
        add document to the positional index
    '''
    def add_to_PI(self, doc_ID, title_arr, plot_arr):
        if not doc_ID in self.df['id']:
            self.df.loc[doc_ID] = [doc_ID, title_arr, plot_arr]
            self.add_to_PI_title(doc_ID, title_arr)
            self.add_to_PI_plot(doc_ID, plot_arr)
        else:
            print('warning: there is a doc_ID like this: ', doc_ID)        

    '''
        add title array to title positional index
    '''
    def add_to_PI_title(self, doc_ID, arr):

        for idx, term in enumerate(arr):
            if term in self.PI_title.keys():
                if doc_ID in self.PI_title[term].keys():
                    self.PI_title[term][doc_ID].append(idx)
                else:
                    self.PI_title[term][doc_ID] = [idx]
            else:
                self.PI_title[term] = {doc_ID: [idx]}
    
    '''
        add title array to plot positional index
    '''
    def add_to_PI_plot(self, doc_ID, arr):
        for idx, term in enumerate(arr):
            if term in self.PI_plot.keys():
                if doc_ID in self.PI_plot[term].keys():
                    self.PI_plot[term][doc_ID].append(idx)
                else:
                    self.PI_plot[term][doc_ID] = [idx]
            else:
                self.PI_plot[term] = {doc_ID: [idx]}
    
    '''
        delete document from positional index with document_ID
    '''
    def delete_from_PI(self, doc_ID):
        if doc_ID in self.df['id']:
            doc = self.df.loc[doc_ID]
            title_arr = doc['title']
            plot_arr = doc['plot']

            for term in title_arr:
                if doc_ID in self.PI_title[term]:
                    self.PI_title[term].pop(doc_ID)
            
            for term in plot_arr:
                if doc_ID in self.PI_plot[term]:
                    self.PI_plot[term].pop(doc_ID)

            self.df.drop(doc_ID, inplace=True)

        else:
            print('warning: there is no doc_ID like this in docs: ', doc_ID)

    '''
        return postional index in other form
    '''

    def get_terms(self):
        terms_set = set()
        terms_set.update(list(self.PI_title.keys()))
        terms_set.update(list(self.PI_plot.keys()))
        return terms_set

    def get_positional_index(self):
        positional_index = {}
        for term in self.PI_title:
            PI_title_arr = []
            for idx in self.PI_title[term]:
                PI_title_arr.append([idx, self.PI_title[term][idx]])

            positional_index[term] = [PI_title_arr, []]
        
        for term in self.PI_plot:
            PI_plot_arr = []
            for idx in self.PI_plot[term]:
                PI_plot_arr.append([idx, self.PI_plot[term][idx]])

            if term in positional_index.keys():
                positional_index[term][1] = PI_plot_arr

            else:
                positional_index[term] = [[], PI_plot_arr]

        return positional_index

def create_positional_index(without_stop_words_df):
    """Creates positional index for both title and plot
    
    positional_index = {'term': [title_posting_list, plot_posting_list]}
    posting_list = [[doc_1_id, [doc_1_occurrance_index_1, ...]], [doc_2_id, [doc_2_occurrance_index_1, ...]], ...]
    doc_ids and doc_occurrence_indexes are sorted

    parameters
    ----------
    without_stop_words_df: data frame with out stop words

    Returns
    -------
    dict
         The created positional_index
    """

    positional_index = Positional_Index()
    df_size = without_stop_words_df.shape[0]
    for i in range(df_size):
        doc = without_stop_words_df.iloc[i]
        positional_index.add_to_PI(int(doc['id']), doc['title'], doc['plot'])
    
    return positional_index

In [30]:
'''
    positional index from movies_df
    it returns in and other format
'''
PI = create_positional_index(with_out_stop_words_df)
PI.get_positional_index()

{'suburbanit': [[[0, [0]]], []],
 'laugh': [[[1, [0]],
   [371, [0]],
   [372, [0]],
   [591, [0]],
   [1672, [3]],
   [2352, [0]],
   [3016, [1]],
   [3532, [1]]],
  [[1, [7, 17]],
   [26, [84]],
   [121, [47]],
   [131, [55]],
   [143, [91]],
   [161, [91]],
   [176, [25]],
   [200, [159]],
   [232, [100, 213]],
   [374, [112]],
   [402, [152]],
   [432, [170]],
   [451, [124]],
   [456, [181]],
   [536, [135]],
   [552, [118]],
   [591, [23, 58, 69]],
   [697, [27]],
   [841, [436, 748]],
   [1045, [423]],
   [1105, [88]],
   [1205, [283, 1585]],
   [1289, [137]],
   [1298, [258]],
   [1345, [90]],
   [1375, [113]],
   [1587, [170]],
   [1670, [205]],
   [1783, [20]],
   [1849, [274]],
   [1905, [44]],
   [2022, [102]],
   [2053, [57]],
   [2240, [377]],
   [2268, [97]],
   [2311, [111]],
   [2348, [41]],
   [2389, [80]],
   [2508, [536]],
   [2626, [392]],
   [2638, [29]],
   [2722, [117]],
   [2734, [133]],
   [2753, [190]],
   [2780, [370]],
   [2875, [278]],
   [2974, [323]],
  

# Dynamization of Indexes

In [33]:
def add_single_documnet(positional_index, stop_words, document):
    """Adds a document to positional index

    Parameters
    ----------
    positional_index: Positional_Index
        target positional index
    stop_words: str array
        stop words
    document : str
        Comma separated string containing id,title,plot in this exact order
    """

    # TODO: implement adding a document to the index
    id, title, plot = document.split(',')
    id = int(id)
    title_arr = delete_stop_words_from_array(prepare_text(title), stop_words)
    plot_arr = delete_stop_words_from_array(prepare_text(plot), stop_words)

    positional_index.add_to_PI(id, title_arr, plot_arr)

In [34]:
'''
    test add_singel_document
'''
new_document = "1234,The Adventures of Sherlock Holmes,The picture begins with Moriarty and Holmes verbally sparring on the steps"
PI2 = Positional_Index()
print('before:', PI2.get_positional_index())
add_single_documnet(PI2, stop_words, new_document)
print('after:')
PI2.get_positional_index()

before: {}
after:


{'adventur': [[[1234, [0]]], []],
 'sherlock': [[[1234, [1]]], []],
 'holm': [[[1234, [2]]], [[1234, [3]]]],
 'pictur': [[], [[1234, [0]]]],
 'begin': [[], [[1234, [1]]]],
 'moriarti': [[], [[1234, [2]]]],
 'verbal': [[], [[1234, [4]]]],
 'spar': [[], [[1234, [5]]]],
 'step': [[], [[1234, [6]]]]}

In [35]:
def remove_single_document(positional_index, document_id):
    """removes a document from positional index

    Parameters
    ----------
    positional_index: Positional_Index
        target positional index
    document_id : int
        Id of the document
    """


    positional_index.delete_from_PI(document_id)
    return

In [36]:
print('before:', PI2.get_positional_index(), sep='\n')
remove_single_document(PI2, 1234)
print('after:', PI2.get_positional_index(), sep='\n')

before:
{'adventur': [[[1234, [0]]], []], 'sherlock': [[[1234, [1]]], []], 'holm': [[[1234, [2]]], [[1234, [3]]]], 'pictur': [[], [[1234, [0]]]], 'begin': [[], [[1234, [1]]]], 'moriarti': [[], [[1234, [2]]]], 'verbal': [[], [[1234, [4]]]], 'spar': [[], [[1234, [5]]]], 'step': [[], [[1234, [6]]]]}
after:
{'adventur': [[], []], 'sherlock': [[], []], 'holm': [[], []], 'pictur': [[], []], 'begin': [[], []], 'moriarti': [[], []], 'verbal': [[], []], 'spar': [[], []], 'step': [[], []]}


# Saving and Compressing Indexes

In [37]:
class JSON_Tool:

    def __jnit__(self):
        pass

    def save_file(self, path, positional_index):
        P_dic = {}
        P_dic['PI_title'] = positional_index.PI_title
        P_dic['PI_plot'] = positional_index.PI_plot
        P_dic['df'] = positional_index.df.to_dict()
        
        with open(path, 'w') as outfile:
            json.dump(P_dic, outfile)

    def load_file(self, path):
        PI = Positional_Index()
        with open(path) as json_file:
            data = json.load(json_file)
            PI.PI_title = data['PI_title']
            PI.PI_plot = data['PI_plot']
            PI.df = pd.DataFrame.from_dict(data['df'])

        return PI

    def get_PI_size(self, positional_index):
        PI_size = 0
        '''
            PI.PI_title
        '''
        PI_size += sys.getsizeof(positional_index.PI_title)
        for term in positional_index.PI_title.keys():
            PI_size += sys.getsizeof(positional_index.PI_title[term])
            for idx in positional_index.PI_title[term].keys():
                PI_size += sys.getsizeof(positional_index.PI_title[term][idx])

        '''
            PI.PI_plot
        '''
        PI_size += sys.getsizeof(positional_index.PI_plot)
        for term in positional_index.PI_plot.keys():
            PI_size += sys.getsizeof(positional_index.PI_plot[term])
            for idx in positional_index.PI_plot[term].keys():
                PI_size += sys.getsizeof(positional_index.PI_plot[term][idx])

        '''
            PI.df
        '''
        PI_size += sys.getsizeof(positional_index.df)
        
        return PI_size



In [38]:
class Compressor:

    def __init__(self):
        pass

    def int_to_byte(self, number):
        bytes_list = []
        while True:
            bytes_list.insert(0, number % 128)
            if number < 128:
                break
            number = number // 128
        bytes_list[-1] += 128
        return pack('%dB' % len(bytes_list), *bytes_list)

    def int_hash_to_byte(self, number):
        bytes_list = []
        while True:
            bytes_list.insert(0, number % 256)
            if number < 256:
                break
            number = number // 256
        return pack('%dB' % len(bytes_list), *bytes_list)

    def arr_to_byte(self, arr):
        int_hash = b''
        for val in arr:
            int_hash = int_hash + self.int_to_byte(val)
        return int_hash

    def stream_to_int(self, stream):
        return int.from_bytes(stream, 'big')

    def stream_to_arr(self, bytestream):
        n = 0
        numbers = []
        bytestream = unpack('%dB' % len(bytestream), bytestream)
        for byte in bytestream:
            if byte < 128:
                n = 128 * n + byte
            else:
                n = 128 * n + (byte - 128)
                numbers.append(n)
                n = 0
        return numbers

    def compress_dic(self, dic):
        comp_dic = {}
        for term in dic.keys():
          comp_dic[term] = self.stream_to_int(self.arr_to_byte(dic[term]))
        return comp_dic

    def variable_byte_encode(self, positional_index):
        '''
            parameter
            ---------
            posititional_index: Positional_Index
                target posititional_index

            return
            ------
            comp_PI: Positional_index
                compressed posititional_index
        '''

        comp_PI = Positional_Index()

        '''
            positional_index.PI_title
        '''
        for term in positional_index.PI_title.keys():
            comp_PI.PI_title[term] = {}
            for idx in positional_index.PI_title[term].keys():
                standard_arr = positional_index.PI_title[term][idx]
                l_arr = len(standard_arr)
                diff_arr = []
                
                if l_arr > 0:
                    diff_arr.append(standard_arr[0])
                if l_arr > 1:
                    for i in range(1,l_arr):
                        diff_arr.append(standard_arr[i] - standard_arr[i-1])

                comp_arr = self.stream_to_int(self.arr_to_byte(diff_arr))
                comp_PI.PI_title[term][idx] = comp_arr

        '''
            positional_index.PI_plot
        '''
        for term in positional_index.PI_plot.keys():
            comp_PI.PI_plot[term] = {}
            for idx in positional_index.PI_plot[term].keys():
                standard_arr = positional_index.PI_plot[term][idx]
                l_arr = len(standard_arr)
                diff_arr = []
                
                if l_arr > 0:
                    diff_arr.append(standard_arr[0])
                if l_arr > 1:
                    for i in range(1,l_arr):
                        diff_arr.append(standard_arr[i] - standard_arr[i-1])

                comp_arr = self.stream_to_int(self.arr_to_byte(diff_arr))
                comp_PI.PI_plot[term][idx] = comp_arr 

        '''
            positional_index.df
        '''            
        comp_PI.df = positional_index.df.copy()

        return comp_PI

    def variable_byte_decode(self, CPI):
        '''
            parameter
            ---------
            CPI: Positional_index 
                compressed positional index

            return
            ------
            PI : Positional_index
                decode positional_index
        '''

        PI = Positional_Index()

        '''
            CPI.PI_title
        '''
        for term in CPI.PI_title.keys():
            PI.PI_title[term] = {}
            for idx in CPI.PI_title[term].keys():
                int_hash = CPI.PI_title[term][idx]
                var_arr = self.stream_to_arr(self.int_hash_to_byte(int_hash))
                var_arr_size = len(var_arr)
                re_arr = [0 for i in range(var_arr_size)]

                if var_arr_size > 0:
                    re_arr[0] = var_arr[0]
                    for i in range(1, var_arr_size):
                        re_arr[i] = re_arr[i-1] + var_arr[i]

                PI.PI_title[term][idx] = re_arr
        
        '''
            CPI.PI_plot
        '''
        for term in CPI.PI_plot.keys():
            PI.PI_plot[term] = {}
            for idx in CPI.PI_plot[term].keys():
                int_hash = CPI.PI_plot[term][idx]
                var_arr = self.stream_to_arr(self.int_hash_to_byte(int_hash))
                var_arr_size = len(var_arr)
                re_arr = [0 for i in range(var_arr_size)]

                if var_arr_size > 0:
                    re_arr[0] = var_arr[0]
                    for i in range(1, var_arr_size):
                        re_arr[i] = re_arr[i-1] + var_arr[i]

                PI.PI_plot[term][idx] = re_arr
        
        '''
            CPI.df
        '''
        PI.df = CPI.df.copy()
        
        return PI

    def gamma_code(self, number):
        length =  int(np.log2(number))
        of_set = bin(number % (2 ** length))[2:]
        l_code = '0'
        for i in range(length):
            l_code = '1' + l_code
        for i in range(length - len(of_set)):
            of_set = '0' + of_set
        
        g_code = l_code + of_set
        return g_code
    
    def gamma_code_to_int(self, g_code):
        return int(g_code, 2)

    def int_to_gamma_code(self, number):
        return bin(number)[2:]

    def gamma_inv(self, g_code):
        size_code = len(g_code)
        if size_code == 1:
            return 1
        pow = int(2 ** ((size_code-1)/2))
        of_set = int(g_code[(size_code+1)//2:], 2)
        return pow + of_set

    def arr_to_int_hash_gamma_code(self, arr):
        gamma = list(map(self.gamma_code, arr))
        gamma_int_hash = list(map(self.gamma_code_to_int, gamma))
        return self.stream_to_int(self.arr_to_byte(gamma_int_hash))

    def int_hash_to_arr_gamama_code(self, int_hash):
        stream = self.int_hash_to_byte(int_hash)
        gamma_arr = list(map(self.int_to_gamma_code, self.stream_to_arr(stream)))
        return list(map(self.gamma_inv, gamma_arr))

    def g_code_encode(self, positional_index):
        '''
            parameter
            ---------
            posititional_index: Positional_Index
                target posititional_index

            return
            ------
            comp_PI: Positional_index
                compressed posititional_index
        '''

        comp_PI = Positional_Index()

        '''
            positional_index.PI_title
        '''
        for term in positional_index.PI_title.keys():
            comp_PI.PI_title[term] = {}
            for idx in positional_index.PI_title[term].keys():
                standard_arr = positional_index.PI_title[term][idx]
                standard_arr = [standard_arr[i] + 1 for i in range(len(standard_arr))]
                comp_PI.PI_title[term][idx] = self.arr_to_int_hash_gamma_code(standard_arr)

        '''
            positional_index.PI_plot
        '''
        for term in positional_index.PI_plot.keys():
            comp_PI.PI_plot[term] = {}
            for idx in positional_index.PI_plot[term].keys():
                standard_arr = positional_index.PI_plot[term][idx]
                standard_arr = [standard_arr[i] + 1 for i in range(len(standard_arr))]
                comp_PI.PI_plot[term][idx] = self.arr_to_int_hash_gamma_code(standard_arr)

        '''
            positional_index.df
        ''' 
        comp_PI.df = positional_index.df.copy()
        
        return comp_PI

    def g_code_decode(self, CPI):
        '''
            parameter
            ---------
            CPI: Positional_index 
                compressed positional index

            return
            ------
            PI : Positional_index
                decode positional_index
        '''

        PI = Positional_Index()

        '''
            CPI.PI_title
        '''
        for term in CPI.PI_title.keys():
            PI.PI_title[term] = {}
            for idx in CPI.PI_title[term].keys():
                int_hash = CPI.PI_title[term][idx]
                standard_arr = self.int_hash_to_arr_gamama_code(int_hash)
                standard_arr = [standard_arr[i] - 1 for i in range(len(standard_arr))]
                PI.PI_title[term][idx] = standard_arr
        '''
            CPI.PI_plot
        '''
        for term in CPI.PI_plot.keys():
            PI.PI_plot[term] = {}
            for idx in CPI.PI_plot[term].keys():
                int_hash = CPI.PI_plot[term][idx]
                standard_arr = self.int_hash_to_arr_gamama_code(int_hash)
                standard_arr = [standard_arr[i] - 1 for i in range(len(standard_arr))]
                PI.PI_plot[term][idx] = standard_arr
 
        '''
            CPI.df
        '''
        PI.df = CPI.df.copy()

        return PI

    def decimal_to_binary(self, n):
        return int(bin(n).replace('0b', ''))

    def binary_to_decimal(self, n):
        return int(str(n), 2)

In [39]:
def store_index(path, compression_type, positional_index):
    """Stores the index in a file

    Parameters
    ----------
    path : str
        Path to store the file

    compression_type : str
        Could be one of the followings:
        - no-compression
        - gamma-code
        - variable-byte

    Returns
    -------
    int
        The size of the stored file
    """
    
    JT = JSON_Tool()

    if compression_type == 'no-compression':
        JT.save_file(path, positional_index)
        return JT.get_PI_size(positional_index)

    elif compression_type == 'gamma-code':
        comp = Compressor()
        CPI = comp.g_code_encode(positional_index)
        JT.save_file(path, CPI)
        return JT.get_PI_size(CPI)

    elif compression_type == 'variable-byte':
        comp = Compressor()
        CPI = comp.variable_byte_encode(positional_index)
        JT.save_file(path, CPI)
        return JT.get_PI_size(CPI)


In [40]:
PI3 = create_positional_index(with_out_stop_words_df[:40])
comp = Compressor()
PI4 = comp.variable_byte_encode(PI3)

# test

In [41]:
store_index("./v_file.json", "variable-byte", PI3)
store_index("./g_file.json", "gamma-code", PI3)
store_index("./n_file.json", "no-compression", PI3)

685024

In [42]:
def load_index(path, compression_type):
    """Loads the index from a file

    Parameters
    ----------
    path : str
        Path of the file to load from

    compression_type : str
        Could be one of the followings:
        - no-compression
        - gamma-code
        - variable-byte

    return
    ------
    PI: positional_index
        decompressed positional_index
    """

    JT = JSON_Tool()

    if compression_type == 'no-compression':
        return JT.load_file(path)
    elif compression_type == 'gamma-code':
        CPI = JT.load_file(path)
        comp = Compressor()
        return comp.g_code_decode(CPI)
    elif compression_type == 'variable-byte':
        CPI = JT.load_file(path)
        comp = Compressor()
        return comp.variable_byte_decode(CPI)

In [43]:
store_index(d_path + "/file.json", "variable-byte", PI3)
load_index(d_path + "/file.json", "no-compression").PI_plot

{'film': {'0': 128,
  '3': 156,
  '8': 135,
  '13': 8488329,
  '15': 128,
  '17': 38531,
  '25': 128,
  '26': 2291306406,
  '30': 130,
  '35': 8389042,
  '38': 202},
 'about': {'0': 129,
  '7': 43912,
  '9': 35208,
  '16': 197,
  '28': 251,
  '30': 146,
  '37': 190},
 'famili': {'0': 130,
  '4': 153,
  '6': 9144273,
  '24': 49849,
  '25': 38581,
  '30': 172,
  '39': 200},
 'move': {'0': 131, '24': 162, '34': 42184, '39': 9830822},
 'suburb': {'0': 132},
 'hop': {'0': 133},
 'quiet': {'0': 134},
 'life': {'0': 135,
  '8': 144,
  '13': 158,
  '24': 154,
  '28': 418,
  '35': 247,
  '37': 174740,
  '39': 47811},
 'thing': {'0': 136, '37': 468},
 'start': {'0': 35206, '5': 142, '20': 62862, '39': 187},
 'go': {'0': 138,
  '1': 131,
  '9': 156,
  '16': 159,
  '20': 2392324262,
  '24': 44958,
  '30': 174,
  '31': 130,
  '37': 114884,
  '39': 237},
 'wrong': {'0': 139, '7': 237, '13': 136},
 'wife': {'0': 140,
  '15': 147959671725200,
  '17': 8556941,
  '21': 169,
  '24': 139,
  '30': 184,
  '

# Correcting the search question

In [44]:
class Bigram_Index:

    def __init__(self):
        self.characters = list(map(chr, range(97, 123)))
        self.characters.append('$')
        self.bigram_index = {}
        for c1 in self.characters:
            for c2 in self.characters:
                self.bigram_index[c1+c2] = []

    def get_word_grams(self, word):
        bg_word = '$' + word + '$'
        grams = [bg_word[i:i+2] for i in range(len(bg_word)-1)]
        return grams

    def add_word(self, word):
        grams = self.get_word_grams(word)
        for g in grams:
            if g[0] in self.characters and g[1] in self.characters:
                self.bigram_index[g].append(word)
            else:
                self.bigram_index[g] = [word]

    def get_related_words(self, word, related_count):
        grams = self.get_word_grams(word)
        related_words = set()
        for g in grams:
            if g in self.bigram_index.keys():
                for w in self.bigram_index[g]:
                    related_words.add(w)

        #it can be better
        related_words = list(related_words)
        scores = []
        for w in related_words:
            scores.append(self.jaccard_metric(word, w))

        sorted_scores = list(sorted(scores, reverse=True))
        
        selected_words = []
        for idx, s in enumerate(scores):
            if s >= sorted_scores[related_count -1]:
                selected_words.append(related_words[idx])

        return selected_words

    def jaccard_metric(self, word1, word2):
        grams1_set = set(self.get_word_grams(word1))
        grams2_set = set(self.get_word_grams(word2))
        return len(set.intersection(grams1_set, grams2_set))/len(set.union(grams1_set, grams2_set))
    
    def correct_term(self, term):
        related_count = 10
        word = prepare_text(term)[0]
        related_words = self.get_related_words(term, related_count)
        min_error = float('inf')
        best_words = word
        for w in related_words:
            error = nltk.edit_distance(word, w)
            if error < min_error:
                best_words = w
                min_error = error

        return best_words
        

    def mark_words(self, string):
        ans = ''
        word = ''
        for i in range(len(string)):
            if string[i].isalpha():
                word += string[i]
            else:
                if len(word) != 0:
                    mark_word = '^' + word + '^'
                    ans += mark_word
                    word = ''
                
                ans += string[i]
                    
        if len(word) != 0:
            ans += '^' + word + '^'

        return ans

    def correct_string(self, raw_string):
        string = self.mark_words(raw_string)

        ans = ''
        word = ''
        flag = False
        for i in range(len(string)):
            if flag:
                if string[i] == '^':
                    flag = False
                    re_word = self.correct_term(word)
                    ans += re_word
                    word = ''
                else:
                    word += string[i]
            else:
                if string[i] == '^':
                    flag = True
                else:    
                    ans += string[i]
        return ans
    

def create_bigram_index(terms):
    """Creates the bigram index for spell correction
    parameter
    ---------
    terms: str array
        words of dictionary

    return
    ------
    bigram_index: Bigram_Index
    """

    BI = Bigram_Index()
    for term in terms:
        BI.add_word(term)

    return BI

def get_all_terms(DataFrame):    
    words = {}
    df_size = DataFrame.shape[0]
    for i in range(df_size):
        arr_title = prepare_text(DataFrame.iloc[i]['title'])
        arr_plot = prepare_text(DataFrame.iloc[i]['plot'])

        for term in arr_title:
            if term in words.keys():
                words[term] += 1
            else:
                words[term] = 1

        for term in arr_plot:
            if term in words.keys():
                words[term] +=1
            else:
                words[term] = 1

    return words.keys()

In [45]:
'''
    create all terms
'''

all_terms = get_all_terms(movie_df)

In [48]:
'''
    create bigram index from positional index terms
'''
BI = create_bigram_index(all_terms)

In [49]:
def get_corrected_text(bigram_index, raw_text):
    """Corrects the query

    Parameters
    ----------
    bigram_index: Bigram_Index
        target bigram index
    stop_words: str array
        stop words
    raw_text : str
        Input text that could be a title or a plot
    Returns
    -------
    str
        The corrected text
    """
    
    return bigram_index.correct_string(raw_text)

get_corrected_text(BI, "the adevntures of herlock holmes")

'the adventur of hemlock holm'

# Searching and Retrieving Documents

In [50]:
class Search_Index:

    def __init__(self, positional_index, stop_words, data_frame):
        self.positional_index = positional_index
        self.PI_size = len(positional_index.get_terms())
        self.doc_count = positional_index.df.shape[0]
        self.stop_words = stop_words
        self.data_frame = data_frame

    def get_tf_title(self, term, doc_ID):
        if term in self.positional_index.PI_title.keys():
            if doc_ID in self.positional_index.PI_title[term].keys():
                return len(self.positional_index.PI_title[term][doc_ID])
        return 0

    def get_tf_plot(self, term, doc_ID):
        if term in self.positional_index.PI_plot.keys():
            if doc_ID in self.positional_index.PI_plot[term].keys():
                return len(self.positional_index.PI_plot[term][doc_ID])
        return 0

    def get_df_title(self, term):
        if term in self.positional_index.PI_title.keys():
            return len(self.positional_index.PI_title[term])
        return 0

    def get_df_plot(self, term):
        if term in self.positional_index.PI_plot.keys():
            return len(self.positional_index.PI_plot[term])
        return 0

    def logarithm(self, val):
        if val == 0:
            return 0
        else:
            return 1 + np.log10(val)

    def inv_freq(self, count, N):
        if count == 0:
            return 0
        else:
            return np.log10(N/count)

    def get_query_dic(self, query):
        dic = {}
        query_words = prepare_text(query)
        query_words = delete_stop_words_from_array(query_words, self.stop_words)
        
        for term in query_words:
            if term in dic.keys():
                dic[term] += 1
            else:
                dic[term] = 1

        return dic

    def get_score_doc(self, title_query, plot_query, title_weight, doc_ID):
        title_q_dic = self.get_query_dic(title_query)
        plot_q_dic = self. get_query_dic(plot_query)
        
        score = 0
        for term in title_q_dic:
            score += title_weight * self.logarithm(title_q_dic[term]) * self.logarithm(self.get_tf_title(term, doc_ID)) * self.inv_freq(self.get_df_title(term), self.doc_count)

        for term in plot_q_dic:
            score += self.logarithm(plot_q_dic[term]) * self.logarithm(self.get_tf_plot(term, doc_ID)) * self.inv_freq(self.get_df_plot(term), self.doc_count)

        return score

    def mark_words(self, string):
        ans = ''
        word = ''
        for i in range(len(string)):
            if string[i].isalpha():
                word += string[i]
            else:
                if len(word) != 0:
                    mark_word = '^' + word + '^'
                    ans += mark_word
                    word = ''
                
                ans += string[i]
                    
        if len(word) != 0:
            ans += '^' + word + '^'

        return ans

    def high_light_string(self, terms, raw_string):
        string = self.mark_words(raw_string)

        ans = ''
        word = ''
        flag = False
        for i in range(len(string)):
            if flag:
                if string[i] == '^':
                    flag = False
                    if prepare_text(word)[0] in terms:
                        ans += '<b>' + word + '</b>'
                    else:    
                        ans += word
                    word = ''
                else:
                    word += string[i]
            else:
                if string[i] == '^':
                    flag = True
                else:    
                    ans += string[i]
        return ans

    def get_doc_result(self, title_query_terms, plot_query_terms, doc_ID):
        doc = self.data_frame.iloc[doc_ID]
        doc_title = doc['title']
        doc_plot = doc['plot']

        return [doc_ID+1, self.high_light_string(title_query_terms, doc_title), self.high_light_string(plot_query_terms, doc_plot)]

    def get_most_relative(self, title_query, plot_query, title_weight, relative_count):
        score_arr = []
        doc_IDs = list(self.positional_index.df['id'])
        for id in doc_IDs:
            score_arr.append((id, self.get_score_doc(title_query, plot_query, title_weight, id)))
        
        sorted_score = list(sorted(score_arr, key= lambda x: x[1], reverse=True))
        
        title_terms = self.get_query_dic(title_query).keys()
        plot_terms = self.get_query_dic(plot_query).keys()
        result = []

        for i in range(relative_count):
            result.append(self.get_doc_result(title_terms, plot_terms, sorted_score[i][0]))
        
        return result
        

In [51]:
def search(positional_index, stop_words, df, title_query, plot_query, title_weight, max_result_count=10):
    """Finds relevant documents to query

    Parameters
    ----------
    positional_index: Positional_Index
    
    df: pd DataFrame
        source dataframe

    stop_words: str array

    title_query : str
        Query to search in titles

    plot_query : str
        Query to search in plots

    title_weight : int
        Defines the significance of title

    max_result_count : int
        Max number of retrieved documents
    
    Returns
    -------
    list
        Retreived documents with snippet
    """
    SI = Search_Index(positional_index, stop_words, df)
    return SI.get_most_relative(title_query, plot_query, title_weight, max_result_count)

In [52]:
PI3 = create_positional_index(with_out_stop_words_df)
search(PI3, stop_words, movie_df, 'madness abandonment ', 'money with bank', 2, 5)

[[40,
  'The <b>Abandonment</b>',
  "Dr. Edmund B. Stewart is a talented young physician who is working hard to build both his professional reputation and practice. He is engaged to Emily Thurston whose father is said to be wealthy. The Thurstons move in the best social circles and Emily is congratulated because her fiance is a successful man. Emily loves Edmund, but is unhappy at the amount of time he spends working at his practice. Stewart's work schedule has caused her to miss many social engagements.[8]\r\nEmily grows resentful that his dedication to duty has curtailed so much of her social life; she starts spending time with Benson Heath. Heath, who has no real job, is attracted to Emily because he believes her family is quite wealthy. He has recently lost a considerable amount of <b>money</b> through bad investments. Heath convinces Emily to break her engagement to Edmund Stewart and asks her to marry him. Stewart, who had been driving himself to work harder, is at the point of e

# Evaluating Performance of System

In [68]:
def precision(actual, predicted):
    return len(set(actual).intersection(set(predicted))) / len(predicted)


def recall(actual, predicted):
    return len(set(actual).intersection(set(predicted))) / len(actual)


def f1_score(actual, predicted):
    p = precision(actual , predicted)
    r = recall(actual , predicted)

    try:
      return (2 * p * r) / (p + r)
    except:
      return 0
    

def map_score(actual, predicted):
    x , score , correct = 0 , 0 , 0
    for doc in predicted:
        x += 1
        if doc in actual:
            correct += 1
            score += (correct) / x
    return score / len(actual)


def ndcg_score(actual, predicted):

    up = 0
    for i in range(len(predicted)):
        if predicted[i] in actual :
            up += 1/np.log2(i+2)

    down = 0
    for i in range(len(actual)):
        down += 1 / np.log2(i+2)

    return float(up / down)

In [73]:
queries = None
with open('./validation.json', 'r', encoding='utf-8') as f:
    queries = json.load(f)
    f.close()

ans = pd.DataFrame(columns = ["precision" , "recall" , "f1" , "map" , "ndcg"])

for query in queries:
    
    actual_docs = query['doc_ids']
    title_query = query['title_query']
    plot_query = query['plot_query']
    title_weight = query['title_weight']
    max_size = query['max_size']

    predicted = search(PI3, stop_words, movie_df, title_query , plot_query, title_weight, max_size)
    
    doc_predicted = []
    for i in range(len(predicted)):
        doc_predicted.append(predicted[i][0])
    
    row = {'f1': f1_score(actual_docs, doc_predicted), 'map' : map_score(actual_docs, doc_predicted) , 'ndcg' : ndcg_score(actual_docs, doc_predicted) ,
        'precision' : precision(actual_docs, doc_predicted) , 'recall' : recall(actual_docs, doc_predicted)}
     
    ans.loc[ans.shape[0]] = row
    
ans

precision    recall        f1       map      ndcg
0   0.900000  0.900000  0.900000  0.900000  0.936379
1   1.000000  1.000000  1.000000  1.000000  1.000000
2   1.000000  1.000000  1.000000  1.000000  1.000000
3   0.833333  0.833333  0.833333  0.801852  0.883283
4   0.000000  0.000000  0.000000  0.000000  0.000000
5   0.000000  0.000000  0.000000  0.000000  0.000000
6   0.000000  0.000000  0.000000  0.000000  0.000000

# Final Words

In [70]:
print(prepare_text("Also, his name is Ali"))
print(get_corrected_text(BI, "Girl whith thiroid Caner meet a boy and fall in love with himm. finaly the girl dyes."))

['also', 'hi', 'name', 'be', 'ali']
girl writh thyroid vaner meet a boy and fall in love with gimm. final the girl dye.


In [74]:
test_case = [
  {
    "max_size": 8,
    "plot_query": "the Scorpion King leads his army on a campaign to conquer the world.",
    "title_query": "The Mummy Returns",
    "title_weight": 1
  },
  {
    "max_size": 4,
    "plot_query": "Jeremy takes John to a wedding for a daughter of the U.S. Secretary of the Treasury\nJohn and Jeremy become acquainted with the Clearys at their home.",
    "title_query": "",
    "title_weight": 1
  },
  {
    "max_size": 10,
    "plot_query": "One of them, later known as The Fallen, defies their sole rule to never destroy planets hosting life by establishing a Sun Harvester on Earth. ",
    "title_query": "",
    "title_weight": 1
  },
  {
    "max_size": 11,
    "plot_query": "jim and his mother are in a birthday celebration. he finds a mysterious map but a sailor with one leg looks for it too. The pirates want to kill Jim. Silver protects him. Jim frees Silver. As he sails away, Silver promises to hunt treasure with Jim again some day.",
    "title_query": "Treasure Island",
    "title_weight": 4
  },
  {
    "max_size": 2,
    "plot_query": "Neo, humanity's only hope of stopping the war and saving Zion, attempts to broker peace between the machines and humans.",
    "title_query": "",
    "title_weight": 4
  },
  {
    "max_size": 8,
    "plot_query": "Captain Jean Luc Picard awaken from a nightmare.\nThe Enterprise arrives in time to assist the crew of the USS Defiant and its captain.\nThe Enterprise arrives hundreds of years in its past on April 4, 2063, the day before humanity's first encounter with alien life.",
    "title_query": "Star Trek",
    "title_weight": 4
  },
  {
    "max_size": 13,
    "plot_query": "In a murder trial, 12 men act as the jury to decide whether or not the boy is guilty for murdering his father. The lawyers won't help the boy as he has a weapon.",
    "title_query": "",
    "title_weight": 4
  },
]

In [208]:
from io import StringIO
from IPython.core.display import display, HTML

res = []
for test in test_case:
    display(HTML(f"<div><b>Title:</b> {test['title_query']}</div>"))
    display(HTML(f"<div><b>Plot:</b> {test['plot_query']}</div>"))
    res = search(PI3, stop_words, movie_df, test['title_query'], test['plot_query'], test['title_weight'], test['max_size'])
    predicted = [x[0] for x in res]
    display(HTML(f"<div><b>Predicted:</b> {predicted}</div>"))
    for i, x in enumerate(res[:2]):
        display(HTML(f"<div><b>{i+1}:</b></div>"))
        display(HTML(f"<div>{x[1]}</div>"))
        display(HTML(f"<div>{x[2]}</div><br>"))
    display(HTML(f"<hr>"))
    res.append(predicted)
res

/tmp/ipykernel_18415/816748511.py:2: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


In [75]:
(precision([1, 2, 3], [1, 4, 2, 5, 3]),
recall([1, 2, 3], [1, 4, 2, 5, 3]),
f1_score([1, 2, 3], [1, 4, 2, 5, 3]),
map_score([1, 2, 3], [1, 4, 2, 5, 3]),
ndcg_score([1, 2, 3], [1, 4, 2, 5, 3]))

(0.6, 1.0, 0.7499999999999999, 0.7555555555555555, 0.8854598815714874)

In [77]:
add_single_documnet(PI2, stop_words, "11567,The Dark Knight,When the menace known as the Joker wreaks havoc and chaos on the people of Gotham")
# add_single_documnet(PI2, stop_words, new_document)
print(search(PI3, stop_words, movie_df,"The Dark Knight", "", 1, 4))
# store_index(d_path + "/file.json", "variable-byte", PI3)
# load_index(d_path + "/file.json", "no-compression").PI_plot

print(store_index(d_path + "nc.json", "no-compression", PI3))
print(store_index(d_path + "gc.json", "gamma-code", PI3))
print(store_index(d_path + "vb.json", "variable-byte", PI3))

remove_single_document(PI3, 11567)
print(search(PI3, stop_words, movie_df,"The Dark Knight", "", 1, 4))

load_index(d_path + "gc.json", "gamma-code").PI_plot
print(search(PI3, stop_words, movie_df,"The Dark Knight", "", 1, 4))

[[2051, '<b>Knights</b> of the Round Table', "With the land in anarchy, warring overlords, Arthur Pendragon (Mel Ferrer) and his half-sister Morgan LeFay (Anne Crawford) meet as arranged by the sorcerer Merlin (Felix Aylmer) to discuss how to end the bloodshed. Morgan maintains that as she is the only legitimate offspring of the late king, the throne belongs to her, but Merlin puts the adversaries to a test to determine England's rightful ruler. Merlin leads them to Excalibur, a sword embedded in an anvil, and says that according to legend, whoever can remove the sword shall be England's true sovereign. Morgan's knight champion Modred (Stanley Baker) tries in vain to extract the sword, but Arthur removes it easily. Modred accuses Merlin of witchcraft, and a hearing is arranged with the Council of Kings at the circle of the stone. After advising Arthur that he must prove himself worthy of the throne by his deeds, Merlin instructs him to return the sword to the stone.\r\nMeanwhile, the F